# Program `DSQ`
## Programed by Tokuro Fukui

In [ ]:
#--------
# Module
#--------
import sys
import math
import numpy as np
import matplotlib.pyplot as plt

# Tips for exercise
- 重陽子を井戸型ポテンシャルで解こう
- 直下のセルにある井戸型ポテンシャルのパラメータを自分でサーチしてみよう
    - `v0`: ポテンシャルの深さ
    - `r0`: ポテンシャルの半径
    - 現時点で`v0`と`r0`には適当な値が代入されている

In [ ]:
#-----------------
# Input variables
#-----------------
## Physical constants
pi = math.pi
hc = 197.3269601               # \hbar c (MeV fm)
m_p = 938.2720                 # Proton mass (MeV)
m_n = 939.5654                 # Neutron mass (MeV)
muac = m_p * m_n / (m_p + m_n) # Reduce mass (MeV)

## Potential parameters
v0 = 10.0 # Depth (MeV)
r0 = 1.0 # Radius (fm)

## Search condition
dk = 0.000001    # Increment (fm^-1)
nb_lim = 10      # Limit of search for bound-state numbers
einf = np.finfo(float).eps # Infinitesimal number

## Wave function
rmx = 20.0   # Norm check (fm)
dr = 0.1     # Increment (fm)

## Scattering length
k0 = math.sqrt(2.0 * muac * v0) / hc
asc = r0 * (1.0 - math.tan(k0 * r0) / (k0 * r0))
print("Scattering length at v0 = ", '{:.10e}'.format(v0 ), "MeV ==>", '{:.5e}'.format(asc), "fm")

## Scattering length variation
v0mn = 1.0
v0mx = 100.0
dv0 = 0.01
iv0mx = int((v0mx-v0mn) / dv0) + 1
ascmx = 100
v0_search = [0] * iv0mx
asc_search = [0] * iv0mx
for iv0 in range(iv0mx):
    v0_search[iv0] = iv0 * dv0 + v0mn
    k0_search = math.sqrt(2.0 * muac * v0_search[iv0]) / hc
    asc_search[iv0] = r0 * (1.0 - math.tan(k0_search * r0) / (k0_search * r0))

    if abs(asc_search[iv0]) > 100.0:
        asc_search[iv0] = np.nan

fig, ax1 = plt.subplots()
ax1.plot(v0_search, asc_search, linewidth=3)
ax1.axvline(x=v0, color='magenta', linestyle='--')

ax1.set_xlim(0, v0mx + 1.0)
ax1.set_ylim(-ascmx, ascmx)
ax1.spines['bottom'].set_position(('data', 0))
ax1.spines['top'].set_visible(False)
plt.xticks(np.arange(0, v0mx + 1.0, step=5))
ax1.set_xlabel("v0 (MeV)")
ax1.set_ylabel("a (fm)")
plt.show()

In [ ]:
#---------------------------------------
# Search for the number of bound states
#---------------------------------------
## Search
nb_mx = -999
rad = math.sqrt(2.0 * muac * v0) * r0 / hc
vr_cond = 8.0 * muac / (pi * hc)**2 * v0 * r0**2

if rad < pi * 0.5:
    print("!!! No bound states have been found.")
    print("!!! Change v0 and r0: ", v0, r0)
    sys.exit()
else:
    for nb in range(nb_lim):
        bl = (2.0 * nb - 1.0)**2
        bu = (2.0 * nb + 1.0)**2
        if vr_cond > bl and vr_cond <= bu:
            nb_mx = nb

if nb_mx == -999:
    nb_mx = nb_lim
    print("!!! More than ", nb_lim, " bound states have been found.")
    print("!!! Lower ", nb_lim, " states are considered.")

print("Number of bound states = ", nb_mx)

## Visualization
kmx = rad / r0
ikmx = int(kmx / dk) + 1

ka = [0] * ikmx
kappa_a_circ = [0] * ikmx
kappa_a_cot  = [0] * ikmx

for ik in range(ikmx):
    k = ik * dk + einf
    ka[ik] = k * r0
    kappa_a_circ[ik] = math.sqrt(2.0 * muac * v0 * r0**2 / hc**2 - (k * r0)**2)
    kappa_a_cot [ik] = -k * r0 * math.cos(k * r0) / math.sin(k * r0)
    if(abs(kappa_a_cot[ik]) > kmx * r0 * 1.2):
        kappa_a_cot [ik] = np.nan

fig, ax1 = plt.subplots()
ax1.plot(ka, kappa_a_circ, label="kappa_a_circ")
ax1.plot(ka, kappa_a_cot, label="kappa_a_cot")

ax1.set_aspect("equal")
ax1.set_xlim(0, kmx * r0 * 1.2)
ax1.set_ylim(0, kmx * r0 * 1.2)

ax1.set_xlabel("ka")
ax1.set_ylabel("$\kappa$a")
ax1.set_title("Plot of kappa_a_circ and kappa_a_cot as a function of ka")
ax1.legend()
plt.show()

In [ ]:
#---------------
# Eigenenergies
#---------------
## Lists
eigk = np.zeros(nb_mx)
eigkappa = np.zeros(nb_mx)
eigkappa_bc = np.zeros(nb_mx)
eige = np.zeros(nb_mx)
anorm = np.zeros(nb_mx)
rrms = np.zeros(nb_mx)
wf = np.zeros(nb_mx)

## Search
nb = -1

for ik in range(ikmx):
    k = ik * dk +einf
    k1 = k - dk
    k2 = k + dk
    xi = k * r0

    xi1 = k1 * r0
    if ik == 0:
        xi1 = xi

    xi2 = k2 * r0
    if ik == ikmx - 1:
        xi2 = xi

    lhs  = math.sqrt(rad**2 - xi **2)
    lhs1 = math.sqrt(rad**2 - xi1**2)
    lhs2 = math.sqrt(rad**2 - xi2**2)

    rhs  = -xi  * math.cos(xi ) / math.sin(xi )
    rhs1 = -xi1 * math.cos(xi1) / math.sin(xi1)
    rhs2 = -xi2 * math.cos(xi2) / math.sin(xi2)

    diff  = abs(lhs  - rhs )
    diff1 = abs(lhs1 - rhs1)
    diff2 = abs(lhs2 - rhs2)

    if diff < diff1 and diff < diff2:
        nb += 1
        eigk[nb] = k - dk

for nb in range(nb_mx):
    eige[nb] = -v0 + (hc * eigk[nb])**2 / (2.0 * muac)
    eigkappa[nb] = math.sqrt(2.0 * muac * abs(eige[nb])) / hc

    if abs(math.tan(eigk[nb] * r0)) < einf:
        deno_kappa_bc = np.sign(math.tan(eigk[nb] * r0)) * einf
    else:
        deno_kappa_bc = math.tan(eigk[nb] * r0)

    eigkappa_bc[nb] = -eigk[nb] / deno_kappa_bc
    anorm[nb] = (eigk[nb] *
                 math.sqrt(2.0 * eigkappa[nb] / (1.0 + eigkappa[nb] * r0)))

    xi = eigk[nb] * r0
    xi_2 = 2.0 * xi
    zeta = eigkappa[nb] * r0

    if abs(eigk[nb]) < einf:
        deno_rrms_sq  = einf
        deno_rrms_sq2 = einf
    else:
        deno_rrms_sq  = 24.0 * eigk[nb]**5
        deno_rrms_sq2 = 4.0 * eigk[nb]**2 * eigkappa[nb]**3

    rrms_sq = (anorm[nb]**2 / deno_rrms_sq
                * (4.0 * xi**3 - 6.0 * xi**2 * math.sin(xi_2)
                    - 6.0 * xi * math.cos(xi_2) + 3.0 * math.sin(xi_2))
                    + anorm[nb]**2 / deno_rrms_sq2
                    * (2.0 * zeta**2 + 2.0 * zeta + 1.0) * math.sin(xi)**2)
    rrms[nb] = math.sqrt(rrms_sq)

## Output
print("-- Eigenstates --")
print("Search for k (0 < k < ", rad/r0, " with ", ikmx, " points)")
print("k        (fm^-1)      = ", eigk)
print("kappa    (fm^-1)      = ", eigkappa)
print("kappa_bc (fm^-1)      = ", eigkappa_bc)
print("E        (MeV)        = ", eige)
print("rRMS     (fm)         = ", rrms)
print("A        (fm^{-3/2})  = ", anorm)

In [ ]:
#---------------
# Wave function
#---------------
## Calculation
irmx = int(rmx / dr) + 1
wf = [[0] * nb_mx for _ in range(irmx)]
norm = [0] * nb_mx
r_val = [0] * irmx

for nb in range(nb_mx):

    for ir in range(irmx):
        r = ir * dr
        r_val[ir] = r
        xi = eigk[nb] * r +einf
        zeta = eigkappa[nb] * r +einf

        if abs(eigk[nb]) < einf:
            deno_bnorm = einf
        else:
            deno_bnorm = eigk[nb]
        bnorm = (-eigkappa[nb] / deno_bnorm
                 * math.exp(eigkappa[nb] * r0)
                 * math.sin(eigk[nb] * r0) * anorm[nb])

        if r < r0:
            wf[ir][nb] = anorm[nb] * math.sin(xi) / xi
        else:
            wf[ir][nb] = -bnorm * math.exp(-zeta) / zeta

        norm[nb] += (r * wf[ir][nb])**2 * dr

print("Norm (up to ", rmx, " fm)   = ", norm)

## Plot
rplt_add = 2.0
rpltmx = r0 + rplt_add
fig, ax1 = plt.subplots()

rect1 = plt.Rectangle((0, -v0), r0, -10, color='gray', alpha=0.5, linewidth=0)
rect2 = plt.Rectangle((r0, 0), rplt_add, -v0-10, color='gray', alpha=0.5, linewidth=0)
ax1.add_patch(rect1)
ax1.add_patch(rect2)

plot_indices = [i for i, r in enumerate(r_val) if r <= rpltmx]
r_plot = [r_val[i] for i in plot_indices]

for nb in range(nb_mx):
    wf_nb = [30*(wf[i][nb])+eige[nb] for i in plot_indices]
    ax1.plot(r_plot, wf_nb, label=f"nb={nb}")

for energy in eige:
    ax1.plot([0, r0], [energy, energy], linestyle="-", linewidth="3", color="#000000", label=f'Energy={energy} MeV')

ax1.set_xlabel("r (fm)")
ax1.set_ylabel("Wave function / Potential / Energy")
ax1.set_title("Wave Function, Potential, and Energy as a Function of r")
ax1.legend()

plt.show()